In [1]:
import pygame, sys, random
import numpy as np
from keras.layers import Dense
from keras.models import Sequential
from keras.optimizers import Adam
import math
import matplotlib.pyplot as plt
import pylab

num_episodes = 100001

obstacleRadius = 10
agentRadius = 10

# get size of state and action from environment

boundaryPos = [10, 10]
boundaryLength = [70,70]
boundaryRadius = 40
initPosAgent = [boundaryPos[0] + boundaryLength[0] / 2, boundaryPos[1] + boundaryLength[1] / 2]
goalPos = [boundaryPos[0] + boundaryLength[0], boundaryPos[1] + boundaryLength[1]/2]
goalAngle = 0#random.randrange(0, 360) * math.pi / 180

moveObstacles = True
action_size = 9
obsNumber = 1
state_size = obsNumber * 2
# state_size = obsNumber + 1

Using TensorFlow backend.


In [7]:
# A2C(Advantage Actor-Critic) agent
class A2CAgent:
    def __init__(self, state_size, action_size):
        self.load_model = False
        
        # get size of state and action
        self.state_size = state_size
        self.action_size = action_size
        self.value_size = 1

        # These are hyper parameters for the Policy Gradient
        self.discount_factor = 0.99
        self.actor_lr = 0.00002
        self.critic_lr = 0.00005

        # create model for policy network
        self.actor = self.build_actor()
        self.critic = self.build_critic()

        if self.load_model:
            self.actor.load_weights("./Practice004_DataSave/Actor_Rev.h5")
            self.critic.load_weights("./Practice004_DataSave/Critic_Rev.h5")

    # approximate policy and value using Neural Network
    # actor: state is input and probability of each action is output of model
    def build_actor(self):
        actor = Sequential()
        actor.add(Dense(128, input_dim=self.state_size, activation='relu', kernel_initializer='glorot_normal'))
        actor.add(Dense(self.action_size, activation='softmax', kernel_initializer='glorot_normal'))
        actor.summary()
        # See note regarding crossentropy in cartpole_reinforce.py
        actor.compile(loss='categorical_crossentropy', optimizer=Adam(lr=self.actor_lr))
        return actor

    # critic: state is input and value of state is output of model
    def build_critic(self):
        critic = Sequential()
        critic.add(Dense(128, input_dim=self.state_size, activation='relu', kernel_initializer='glorot_normal'))
        critic.add(Dense(self.value_size, activation='linear', kernel_initializer='glorot_normal'))
        critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic

    # using the output of policy network, pick action stochastically
    def get_action(self, state):
        policy = self.actor.predict(state, batch_size=1).flatten()
#         print policy
        return np.random.choice(self.action_size, 1, p=policy)[0]

    # update policy network every episode
    def train_model(self, state, action, reward, next_state, done):
        target = np.zeros((1, self.value_size))
        advantages = np.zeros((1, self.action_size))

        value = self.critic.predict(state)[0]
        next_value = self.critic.predict(next_state)[0]

        if done:
            advantages[0][action] = reward - value
            target[0][0] = reward
        else:
            advantages[0][action] = reward + self.discount_factor * (next_value) - value
            target[0][0] = reward + self.discount_factor * next_value

        self.actor.fit(state, advantages, epochs=1, verbose=0)
        self.critic.fit(state, target, epochs=1, verbose=0)

In [3]:
def ckWall(xPos, yPos):
#     flagWall = 0
#     if(xPos < boundaryPos[0]):
#         xPos = boundaryPos[0]
#         flagWall = -1
#     elif(xPos > boundaryPos[0] + boundaryLength[0]):
#         xPos = boundaryPos[0] + boundaryLength[0]
#         flagWall = -1
#     if(yPos < boundaryPos[1]):
#         yPos = boundaryPos[1]
#         flagWall = -1
#     elif(yPos > boundaryPos[1] + boundaryLeflagWallngth[1]):
#         yPos = boundaryPos[1] + boundaryLength[1]
#         flagWall = -1
    if math.sqrt((xPos - initPosAgent[0]) ** 2 + (yPos - initPosAgent[1]) ** 2) > boundaryRadius - obstacleRadius:
        if xPos - initPosAgent[0] != 0:
            xPos = xPos - (xPos - initPosAgent[0])/abs(xPos - initPosAgent[0])
        if yPos - initPosAgent[1] != 0:
            yPos = yPos - (yPos - initPosAgent[1])/abs(yPos - initPosAgent[1])
    return [int(round(xPos)), int(round(yPos))]

In [4]:
def stateGenerator(obsPosition, agtPosition):
    returnSum = []
    for i in range(0,obsNumber):
        returnSum = returnSum + [agtPosition[0] - obsPosition[i][0], agtPosition[1] - obsPosition[i][1]]
#     returnSum = returnSum + [agtPosition[0] - boundaryRadius * math.cos(goalAngle), agtPosition[1] - boundaryRadius * math.sin(goalAngle)]
    returnSum = np.reshape(returnSum, [1, state_size])
    return returnSum

In [5]:
def takeAction(action):
    xAction = 0
    yAction = 0
    if action == 0:
        xAction = 1
    elif action == 1:
        xAction = 1
        yAction = 1
    elif action == 2:
        xAction = 1
        yAction = -1            
    elif action == 3:
        xAction = -1
        yAction = 1
    elif action == 4:
        xAction = -1
    elif action == 5:
        xAction = -1
        yAction = -1
    elif action == 6:
        yAction = -1
    elif action == 7:
        yAction = 1
    elif action == 8:
        xAction = 0
        yAction = 0
        
    return [xAction, yAction]

In [ ]:
pygame.init()
screen = pygame.display.set_mode([100,100])
screen.fill([200, 200, 200])

# make A2C agent
agent = A2CAgent(state_size, action_size)

rList, episodes = [], []

# Make Obstacles (obsNumber)
obstaclePos = [[0, 0] for _ in range(obsNumber)]
for i in range(0,obsNumber):
    obsRadius = random.randrange(agentRadius + obstacleRadius + 5, boundaryRadius)
    obsAngle = random.randrange(0,360) * math.pi / 180
    obstaclePos[i][0] = int(initPosAgent[0] + obsRadius * math.cos(obsAngle)) #boundaryPos[0] + random.randrange(1, boundaryLength[0])
    obstaclePos[i][1] = int(initPosAgent[1] + obsRadius * math.sin(obsAngle)) #boundaryPos[1] + random.randrange(1, boundaryLength[1])

for e in range(num_episodes):
    # Initialize
    done = False
    score = 0
    x = initPosAgent[0]
    y = initPosAgent[1]
    print("Episode ", e, "Starts!")
    state = stateGenerator(obstaclePos, [x,y])
    #state = np.reshape(state, [1, state_size])
    
    while not done:
        
        action = agent.get_action(state)
        
        xMove = 0
        yMove = 0
        
        [xMove, yMove] = takeAction(action)
        
        x = x + xMove
        y = y + yMove
        
        wallFlag = 0
        collisionFlag = 0
#         [x, y] = ckWall(x, y)
        pygame.draw.circle(screen, [100, 100, 255], [x,y], 10, 0)
        next_state = stateGenerator(obstaclePos, [x,y])

        if(math.sqrt((x - initPosAgent[0])**2 + (y - initPosAgent[1])**2) >= boundaryRadius - agentRadius):
            print("Goal Reached!")
            collisionFlag = 1
            done = True
        for i in range(0,obsNumber):
            if moveObstacles:
                obstaclePos[i][0] = obstaclePos[i][0] + random.randrange(1, 6) * random.randrange(-1,2)
                obstaclePos[i][1] = obstaclePos[i][1] + random.randrange(1, 6) * random.randrange(-1,2)
                [obstaclePos[i][0], obstaclePos[i][1]] = ckWall(obstaclePos[i][0], obstaclePos[i][1])
                
            pygame.draw.circle(screen, [255, 50, 50], obstaclePos[i], 10, 0)
            if math.sqrt((x - obstaclePos[i][0])**2 + (y - obstaclePos[i][1])**2) <= 20:
                print("Collision!")
                collisionFlag = -1
                done = True
        
        if not done:
            reward = 0
        else:
            if collisionFlag == 1:
                reward = -1000 #10000 * math.cos(math.atan2(y - initPosAgent[1], x - initPosAgent[0]))
                rList.append(1)
            elif collisionFlag == -1:
                reward = 1000
                rList.append(0)
        
        agent.train_model(state, action, reward, next_state, done)
        
        score += reward
        state = next_state
#         if score < -1000:
#             score -= 1000
#             done = True
        if done:
            # every episode, plot the play time
            obstaclePos = [[0, 0] for _ in range(obsNumber)]
            for i in range(0,obsNumber):
                obsRadius = random.randrange(agentRadius + 2, boundaryRadius)
                obsAngle = random.randrange(0,360) * math.pi / 180
                obstaclePos[i][0] = int(initPosAgent[0] + obsRadius * math.cos(obsAngle))
                obstaclePos[i][1] = int(initPosAgent[1] + obsRadius * math.sin(obsAngle))

            episodes.append(e)
#             pylab.plot(episodes, rList, 'b')
            
        #circle(Surface, color, pos, radius, width=0)
#         pygame.draw.circle(screen, [100,255,100], [goalPos[0],goalPos[1]], 10, 2)
        #rect(Surface, color, Rect, width=0)
#         pygame.draw.rect(screen, [255,100,100],[boundaryPos[0] - agentRadius, boundaryPos[1] - agentRadius, boundaryLength[0] + agentRadius * 2, boundaryLength[1] + agentRadius * 2],2)
        pygame.draw.circle(screen, [255,100,100], [initPosAgent[0], initPosAgent[1]], boundaryRadius, 2)
        pygame.display.flip()
        screen.fill([200,200,200])
    print score
    # save the model
    if e % 50 == 0:
        agent.actor.save_weights("./Practice004_DataSave/Actor_Rev.h5")
        agent.critic.save_weights("./Practice004_DataSave/Critic_Rev.h5")
#         pylab.savefig("./Practice004_DataSave/ActorCriticGraph.png")

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_5 (Dense)              (None, 128)               384       
_________________________________________________________________
dense_6 (Dense)              (None, 9)                 1161      
Total params: 1,545
Trainable params: 1,545
Non-trainable params: 0
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 128)               384       
_________________________________________________________________
dense_8 (Dense)              (None, 1)                 129       
Total params: 513
Trainable params: 513
Non-trainable params: 0
_________________________________________________________________
('Episode ', 0, 'Starts!')
Collision!
1000
('Episode ', 1, 'Starts!')
Collis

Collision!
1000
('Episode ', 157, 'Starts!')
Goal Reached!
-1000
('Episode ', 158, 'Starts!')
Collision!
1000
('Episode ', 159, 'Starts!')
Collision!
1000
('Episode ', 160, 'Starts!')
Goal Reached!
-1000
('Episode ', 161, 'Starts!')
Collision!
1000
('Episode ', 162, 'Starts!')
Collision!
1000
('Episode ', 163, 'Starts!')
Collision!
1000
('Episode ', 164, 'Starts!')
Collision!
1000
('Episode ', 165, 'Starts!')
Collision!
1000
('Episode ', 166, 'Starts!')
Goal Reached!
-1000
('Episode ', 167, 'Starts!')
Collision!
1000
('Episode ', 168, 'Starts!')
Collision!
1000
('Episode ', 169, 'Starts!')
Collision!
1000
('Episode ', 170, 'Starts!')
Collision!
1000
('Episode ', 171, 'Starts!')
Collision!
1000
('Episode ', 172, 'Starts!')
Collision!
1000
('Episode ', 173, 'Starts!')
Collision!
1000
('Episode ', 174, 'Starts!')
Collision!
1000
('Episode ', 175, 'Starts!')
Collision!
1000
('Episode ', 176, 'Starts!')
Collision!
1000
('Episode ', 177, 'Starts!')
Collision!
1000
('Episode ', 178, 'Starts!'

Collision!
1000
('Episode ', 338, 'Starts!')
Goal Reached!
-1000
('Episode ', 339, 'Starts!')
Collision!
1000
('Episode ', 340, 'Starts!')
Goal Reached!
-1000
('Episode ', 341, 'Starts!')
Collision!
1000
('Episode ', 342, 'Starts!')
Collision!
1000
('Episode ', 343, 'Starts!')
Collision!
1000
('Episode ', 344, 'Starts!')
Collision!
1000
('Episode ', 345, 'Starts!')
Collision!
1000
('Episode ', 346, 'Starts!')
Collision!
1000
('Episode ', 347, 'Starts!')
Collision!
1000
('Episode ', 348, 'Starts!')
Collision!
1000
('Episode ', 349, 'Starts!')
Collision!
1000
('Episode ', 350, 'Starts!')
Collision!
1000
('Episode ', 351, 'Starts!')
Collision!
1000
('Episode ', 352, 'Starts!')
Collision!
1000
('Episode ', 353, 'Starts!')
Collision!
1000
('Episode ', 354, 'Starts!')
Collision!
1000
('Episode ', 355, 'Starts!')
Collision!
1000
('Episode ', 356, 'Starts!')
Collision!
1000
('Episode ', 357, 'Starts!')
Collision!
1000
('Episode ', 358, 'Starts!')
Collision!
1000
('Episode ', 359, 'Starts!')
Co

Collision!
1000
('Episode ', 519, 'Starts!')
Collision!
1000
('Episode ', 520, 'Starts!')
Collision!
1000
('Episode ', 521, 'Starts!')
Collision!
1000
('Episode ', 522, 'Starts!')
Collision!
1000
('Episode ', 523, 'Starts!')
Collision!
1000
('Episode ', 524, 'Starts!')
Collision!
1000
('Episode ', 525, 'Starts!')
Collision!
1000
('Episode ', 526, 'Starts!')
Collision!
1000
('Episode ', 527, 'Starts!')
Collision!
1000
('Episode ', 528, 'Starts!')
Collision!
1000
('Episode ', 529, 'Starts!')
Collision!
1000
('Episode ', 530, 'Starts!')
Collision!
1000
('Episode ', 531, 'Starts!')
Collision!
1000
('Episode ', 532, 'Starts!')
Collision!
1000
('Episode ', 533, 'Starts!')
Collision!
1000
('Episode ', 534, 'Starts!')
Collision!
1000
('Episode ', 535, 'Starts!')
Collision!
1000
('Episode ', 536, 'Starts!')
Goal Reached!
-1000
('Episode ', 537, 'Starts!')
Collision!
1000
('Episode ', 538, 'Starts!')
Collision!
1000
('Episode ', 539, 'Starts!')
Collision!
1000
('Episode ', 540, 'Starts!')
Collis

1000
('Episode ', 702, 'Starts!')
Collision!
1000
('Episode ', 703, 'Starts!')
Collision!
1000
('Episode ', 704, 'Starts!')
Collision!
1000
('Episode ', 705, 'Starts!')
Collision!
1000
('Episode ', 706, 'Starts!')
Collision!
1000
('Episode ', 707, 'Starts!')
Collision!
1000
('Episode ', 708, 'Starts!')
Collision!
1000
('Episode ', 709, 'Starts!')
Collision!
1000
('Episode ', 710, 'Starts!')
Collision!
1000
('Episode ', 711, 'Starts!')
Collision!
1000
('Episode ', 712, 'Starts!')
Collision!
1000
('Episode ', 713, 'Starts!')
Collision!
1000
('Episode ', 714, 'Starts!')
Collision!
1000
('Episode ', 715, 'Starts!')
Collision!
1000
('Episode ', 716, 'Starts!')
Collision!
1000
('Episode ', 717, 'Starts!')
Goal Reached!
-1000
('Episode ', 718, 'Starts!')
Collision!
1000
('Episode ', 719, 'Starts!')
Collision!
1000
('Episode ', 720, 'Starts!')
Collision!
1000
('Episode ', 721, 'Starts!')
Collision!
1000
('Episode ', 722, 'Starts!')
Collision!
1000
('Episode ', 723, 'Starts!')
Collision!
1000
(

...

1000
('Episode ', 75903, 'Starts!')
Collision!
1000
('Episode ', 75904, 'Starts!')
Goal Reached!
-1000
('Episode ', 75905, 'Starts!')
Collision!
1000
('Episode ', 75906, 'Starts!')
Collision!
1000
('Episode ', 75907, 'Starts!')
Collision!
1000
('Episode ', 75908, 'Starts!')
Collision!
1000
('Episode ', 75909, 'Starts!')
Collision!
1000
('Episode ', 75910, 'Starts!')
Collision!
1000
('Episode ', 75911, 'Starts!')
Collision!
1000
('Episode ', 75912, 'Starts!')
Collision!
1000
('Episode ', 75913, 'Starts!')
Collision!
1000
('Episode ', 75914, 'Starts!')
Collision!
1000
('Episode ', 75915, 'Starts!')
Collision!
1000
('Episode ', 75916, 'Starts!')
Collision!
1000
('Episode ', 75917, 'Starts!')
Collision!
1000
('Episode ', 75918, 'Starts!')
Collision!
1000
('Episode ', 75919, 'Starts!')
Collision!
1000
('Episode ', 75920, 'Starts!')
Collision!
1000
('Episode ', 75921, 'Starts!')
Collision!
1000
('Episode ', 75922, 'Starts!')
Collision!
1000
('Episode ', 75923, 'Starts!')
Collision!
1000
('Ep

Collision!
1000
('Episode ', 76077, 'Starts!')
Goal Reached!
-1000
('Episode ', 76078, 'Starts!')
Collision!
1000
('Episode ', 76079, 'Starts!')
Collision!
1000
('Episode ', 76080, 'Starts!')
Collision!
1000
('Episode ', 76081, 'Starts!')
Collision!
1000
('Episode ', 76082, 'Starts!')
Collision!
1000
('Episode ', 76083, 'Starts!')
Collision!
1000
('Episode ', 76084, 'Starts!')
Collision!
1000
('Episode ', 76085, 'Starts!')
Collision!
1000
('Episode ', 76086, 'Starts!')
Collision!
1000
('Episode ', 76087, 'Starts!')
Collision!
1000
('Episode ', 76088, 'Starts!')
Collision!
1000
('Episode ', 76089, 'Starts!')
Collision!
1000
('Episode ', 76090, 'Starts!')
Collision!
1000
('Episode ', 76091, 'Starts!')
Collision!
1000
('Episode ', 76092, 'Starts!')
Collision!
1000
('Episode ', 76093, 'Starts!')
Goal Reached!
-1000
('Episode ', 76094, 'Starts!')
Collision!
1000
('Episode ', 76095, 'Starts!')
Collision!
1000
('Episode ', 76096, 'Starts!')
Collision!
1000
('Episode ', 76097, 'Starts!')
Colli

Collision!
1000
('Episode ', 76252, 'Starts!')
Collision!
1000
('Episode ', 76253, 'Starts!')
Goal Reached!
-1000
('Episode ', 76254, 'Starts!')
Collision!
1000
('Episode ', 76255, 'Starts!')
Collision!
1000
('Episode ', 76256, 'Starts!')
Collision!
1000
('Episode ', 76257, 'Starts!')
Collision!
1000
('Episode ', 76258, 'Starts!')
Collision!
1000
('Episode ', 76259, 'Starts!')
Collision!
1000
('Episode ', 76260, 'Starts!')
Collision!
1000
('Episode ', 76261, 'Starts!')
Collision!
1000
('Episode ', 76262, 'Starts!')
Collision!
1000
('Episode ', 76263, 'Starts!')
Collision!
1000
('Episode ', 76264, 'Starts!')
Collision!
1000
('Episode ', 76265, 'Starts!')
Collision!
1000
('Episode ', 76266, 'Starts!')
Collision!
1000
('Episode ', 76267, 'Starts!')
Collision!
1000
('Episode ', 76268, 'Starts!')
Goal Reached!
-1000
('Episode ', 76269, 'Starts!')
Collision!
1000
('Episode ', 76270, 'Starts!')
Collision!
1000
('Episode ', 76271, 'Starts!')
Collision!
1000
('Episode ', 76272, 'Starts!')
Colli

Collision!
1000
('Episode ', 76428, 'Starts!')
Collision!
1000
('Episode ', 76429, 'Starts!')
Collision!
1000
('Episode ', 76430, 'Starts!')
Collision!
1000
('Episode ', 76431, 'Starts!')
Collision!
1000
('Episode ', 76432, 'Starts!')
Collision!
1000
('Episode ', 76433, 'Starts!')
Collision!
1000
('Episode ', 76434, 'Starts!')
Collision!
1000
('Episode ', 76435, 'Starts!')
Collision!
1000
('Episode ', 76436, 'Starts!')
Collision!
1000
('Episode ', 76437, 'Starts!')
Collision!
1000
('Episode ', 76438, 'Starts!')
Collision!
1000
('Episode ', 76439, 'Starts!')
Collision!
1000
('Episode ', 76440, 'Starts!')
Collision!
1000
('Episode ', 76441, 'Starts!')
Collision!
1000
('Episode ', 76442, 'Starts!')
Collision!
1000
('Episode ', 76443, 'Starts!')
Collision!
1000
('Episode ', 76444, 'Starts!')
Collision!
1000
('Episode ', 76445, 'Starts!')
Collision!
1000
('Episode ', 76446, 'Starts!')
Collision!
1000
('Episode ', 76447, 'Starts!')
Collision!
1000
('Episode ', 76448, 'Starts!')
Collision!
10

Goal Reached!
-1000
('Episode ', 76605, 'Starts!')
Collision!
1000
('Episode ', 76606, 'Starts!')
Collision!
1000
('Episode ', 76607, 'Starts!')
Collision!
1000
('Episode ', 76608, 'Starts!')
Collision!
1000
('Episode ', 76609, 'Starts!')
Collision!
1000
('Episode ', 76610, 'Starts!')
Collision!
1000
('Episode ', 76611, 'Starts!')
Collision!
1000
('Episode ', 76612, 'Starts!')
Collision!
1000
('Episode ', 76613, 'Starts!')
Collision!
1000
('Episode ', 76614, 'Starts!')
Collision!
1000
('Episode ', 76615, 'Starts!')
Collision!
1000
('Episode ', 76616, 'Starts!')
Collision!
1000
('Episode ', 76617, 'Starts!')
Collision!
1000
('Episode ', 76618, 'Starts!')
Collision!
1000
('Episode ', 76619, 'Starts!')
Collision!
1000
('Episode ', 76620, 'Starts!')
Collision!
1000
('Episode ', 76621, 'Starts!')
Collision!
1000
('Episode ', 76622, 'Starts!')
Collision!
1000
('Episode ', 76623, 'Starts!')
Collision!
1000
('Episode ', 76624, 'Starts!')
Collision!
1000
('Episode ', 76625, 'Starts!')
Collision

In [ ]:
print("Percent of successful episodes: " + str(100.0 * sum(rList)/num_episodes) + "%")

# plt.bar(range(len(rList)), rList, color = "Blue", width = 0.00001)
# plt.show()